# Komputerowe wspomaganie tłumaczenia

# Zajęcia 11 - urównoleglanie

Na poprzednich zajęciach poznaliśmy techniki pozyskiwania tekstu z Internetu. Jeśli uda nam się w ten sposób pozyskać tekst w jednym języku oraz jego tłumaczenie na inny język, jesteśmy tylko o krok od uzyskania najbardziej przydatnego zasobu z punktu widzenia wspomagania tłumaczenia - pamięci tłumaczeń. Krokiem tym jest automatyczne urównoleglanie tekstu.

Automatyczne urównoleglanie tekstu składa się z dwóch kroków:
1. Podziału tekstu źródłowego oraz docelowego na zdania.
2. Dopasowaniu zdań źródłowych do docelowych.

Zdania, o których mowa w punkcie 1., powinniśmy rozumieć jako segmenty, tj. niekoniecznie kompletne zdania w sensie gramatycznym. Standardowym sposobem podziału tekstu na segmenty jest dzielenie po znaku nowej linii lub zaraz po kropce, o ile jest ona częścią sekwencji: ".[spacja][Wielka litera]"

### Ćwiczenie 1: Zaimplementuj podstawowy algorytm segmentacji tekstu. Użyj odpowiedniego wyrażenia regularnego, łapiącego wielkie litery w dowolnym języku, np. "Ż" (użyj klasy unikodowej). Zwróć listę segmentów.

In [1]:
import regex

def sentence_split(text):
    # Regular expression pattern to match sentence-ending punctuation followed by a space and an uppercase letter
    pattern = regex.compile(r'(?<=[.!?])\s+(?=\p{Lu})', regex.UNICODE)
    
    # Split the text using the defined pattern
    segments = regex.split(pattern, text)

    # Remove leading and trailing whitespace from each segment
    segments = [segment.strip() for segment in segments]

    # Replace multiple newlines with a single newline
    segments = [regex.sub(r'\n+', '\n', segment) for segment in segments]

    # Replace multiple spaces with a single space
    segments = [regex.sub(r'\s+', ' ', segment) for segment in segments]

    # Remove empty segments
    segments = [segment for segment in segments if segment]
    
    return segments

### Ćwiczenie 2: Uruchom powyższy algorytm na treści wybranej przez siebie strony internetowej (do ściągnięcia treści strony wykorzystaj kod z laboratoriów nr 7). Zidentyfikuj co najmniej dwa wyjątki od ogólnej reguły podziału na segmenty i ulepsz algorytm.

In [2]:
import requests
from bs4 import BeautifulSoup

def fetch_webpage_content(url):
    response = requests.get(url)
    response.raise_for_status()  # Raise an exception for HTTP errors
    soup = BeautifulSoup(response.content, 'html.parser')
    return soup.get_text()

url = "https://wmi.amu.edu.pl/"
webpage_content = fetch_webpage_content(url)

import re
import unicodedata

segments = sentence_split(webpage_content)
for i, segment in enumerate(segments[:10]):
    print(f"Segment {i+1}: {segment}")

Segment 1: Wydział Matematyki i Informatyki | Wydział Matematyki i Informatyki Brak obsługi JavaScript Do pełnej funkcjonalności strony potrzebujesz włączonej obsługi skryptów.
Segment 2: Instrukcje, które pozwolą Ci włączyć skrypty w Twojej przeglądarce znajdziesz tutaj Przejdź do TreśćPrzejdź do Menu głównePrzejdź do Mapa serwisuPrzejdź do Dostępność A A A en pl Wyszukaj Wyszukaj Nawigacja mobilna Wydział - Wydział Matematyki i Informatyki Wydział - Wydział Matematyki i Informatyki NO XML TR1A Wydział Pokaż menu szczegółowe Powrót do głównego menu O wydziale Władze wydziału Struktura wydziału Rada Naukowa Dyscyplin Rady programowe Pracownicy Projekty Historia Biblioteka wydziałowa Informator WMI w mediach Wybory 2024 Kontakt Życie naukowe Pokaż menu szczegółowe Powrót do głównego menu Awanse naukowe Wykłady i seminaria Cykle wykładów Towarzystwa i redakcje Konferencje Doktorzy honoris causa Profesorowie Członkowie Akademii Konkurs im.
Segment 3: Edyty Szymańskiej Dla Kandydata Pokaż 

### Wyjątek 1: Skróty zakończone kropką
Skróty takie jak "mgr.", "prof.", "dr." mogą powodować niepotrzebne podziały segmentów. Musimy upewnić się, że algorytm nie dzieli zdania po skrótach.

### Wyjątek 2: Daty i inne liczby zakończone kropką
Daty, takie jak "22 czerwca 2024 r.", mogą również powodować nieprawidłowe podziały. Musimy uwzględnić takie przypadki.

In [3]:
import regex

def enhanced_sentence_split(text):
    # Lista wyjątków, po których nie dzielimy nawet jeśli jest kropka
    exceptions = ['r.', 'tzn.', 'np.', 'itp.', 'etc.', 'dr.', 'prof.', 'im.']

    # Regular expression pattern to match sentence-ending punctuation followed by a space and an uppercase letter
    pattern = regex.compile(r'(?<=[.!?])\s+(?=\p{Lu})', regex.UNICODE)

    # Split the text using the defined pattern
    segments = regex.split(pattern, text)

    # Remove leading and trailing whitespace from each segment
    segments = [segment.strip() for segment in segments]

    # Rejoin segments that were incorrectly split due to exceptions
    i = 0
    while i < len(segments) - 1:
        for exception in exceptions:
            if segments[i].endswith(exception):
                segments[i] += ' ' + segments.pop(i + 1)
                break
        else:
            i += 1

    # Replace multiple newlines with a single newline
    segments = [regex.sub(r'\n+', '\n', segment) for segment in segments]

    # Replace multiple spaces with a single space
    segments = [regex.sub(r'\s+', ' ', segment) for segment in segments]

    # Remove empty segments
    segments = [segment for segment in segments if segment]

    return segments

segments = enhanced_sentence_split(webpage_content)
for i, segment in enumerate(segments[:10]):
    print(f"Segment {i+1}: {segment}")

Segment 1: Wydział Matematyki i Informatyki | Wydział Matematyki i Informatyki Brak obsługi JavaScript Do pełnej funkcjonalności strony potrzebujesz włączonej obsługi skryptów.
Segment 2: Instrukcje, które pozwolą Ci włączyć skrypty w Twojej przeglądarce znajdziesz tutaj Przejdź do TreśćPrzejdź do Menu głównePrzejdź do Mapa serwisuPrzejdź do Dostępność A A A en pl Wyszukaj Wyszukaj Nawigacja mobilna Wydział - Wydział Matematyki i Informatyki Wydział - Wydział Matematyki i Informatyki NO XML TR1A Wydział Pokaż menu szczegółowe Powrót do głównego menu O wydziale Władze wydziału Struktura wydziału Rada Naukowa Dyscyplin Rady programowe Pracownicy Projekty Historia Biblioteka wydziałowa Informator WMI w mediach Wybory 2024 Kontakt Życie naukowe Pokaż menu szczegółowe Powrót do głównego menu Awanse naukowe Wykłady i seminaria Cykle wykładów Towarzystwa i redakcje Konferencje Doktorzy honoris causa Profesorowie Członkowie Akademii Konkurs im. Edyty Szymańskiej Dla Kandydata Pokaż menu szczeg

Po podziale tekstu na segmenty po stronie źródłowej oraz docelowej, możemy przystąpić do kroku drugiego - dopasowania segmentów. Głównym wyzwaniem tego kroku jest fakt, iż po stronie źródłowej może być inna liczba segmentów, niż po stronie docelowej. Takie rozbieżności są bardzo częste, a wynikają między innymi z:
* tłumaczenia jednego zdania źródłowego przy użyciu więcej niż jednego zdania
* tłumaczenia więcej niż jednego zdania źródłowego przy użyciu jednego zdania
* pominięcia zdania podczas tłumaczenia
* rozbieżności pomiędzy wersjami tekstu źródłowego i docelowego (np. tekst źródłowy mógł być modyfikowany po przetłumaczeniu i tłumaczenie nie zostało zaktualizowane)
* przetłumaczenia tekstu źródłowego tylko częściowo

Problemy te rozwiązwyane są na różne sposoby. Najpopularniejszym programem do przeprowadzania urównoleglania jest [Hunalign](https://github.com/danielvarga/hunalign). Wejściem do programu są dwa pliki, zawierające po jednym segmencie w linii. Wyjściem - plik urównoleglony w wewnętrznym formacie hunaligna.

### Ćwiczenie 3: Odnajdź dowolną stronę, która jest dostępna w wielu językach. Pobierz z tej strony tekst oryginalny (tylko ze strony głównej) oraz przetłumaczony na dowolny inny język. Przy użyciu Pythona przygotuj pliki dla Hunaligna i uruchom go.

Wyjściem z Hunaligna jest plik w specjalnym formacie Hunaligna. Problem jednak w tym, że niestety nie można go w prosty sposób zaimportować do jakiegokolwiek narzędzia typu CAT. Potrzebna jest konwersja do któregoś z bardziej popularnych formatów, np. XLIFF.

XLIFF jest formatem do przechowywania pamięci tłumaczeń, który opiera się na XML-u

In [4]:
text_hu = fetch_webpage_content("https://hu.wikipedia.org/wiki/Sz%C3%A1m%C3%ADt%C3%A1studom%C3%A1ny")
text_en = fetch_webpage_content("https://en.wikipedia.org/wiki/Computer_science")

In [5]:
hu_segments = enhanced_sentence_split(text_hu)
en_segments = enhanced_sentence_split(text_en)

In [6]:
hu_segments

['Számítástudomány – Wikipédia Ugrás a tartalomhoz Főmenü Főmenü áthelyezés az oldalsávba elrejtés Navigáció KezdőlapTartalomKiemelt szócikkekFriss változtatásokLap találomraTudakozó Részvétel KezdőknekSegítségKözösségi portálKapcsolatfelvételAdományok Keresés Keresés Fiók létrehozása Bejelentkezés Személyes eszközök Fiók létrehozása Bejelentkezés Lapok kijelentkezett szerkesztőknek további információk KözreműködésekVitalap Tartalomjegyzék áthelyezés az oldalsávba elrejtés Bevezető 1Vizsgálati területei A(z) Vizsgálati területei alszakasz kinyitása/becsukása 1.1Számítástudomány 1.2Számítógép-tudomány 2Története és alágai 3Kapcsolódó szócikkek 4Jegyzetek 5További információk Tartalomjegyzék kinyitása/becsukása Számítástudomány 161 nyelv EnglishAfrikaansAlemannischአማርኛAragonésالعربيةمصرىঅসমীয়াAsturianuAzərbaycancaتۆرکجهБашҡортсаBoarischŽemaitėškaBikol CentralБеларускаяБеларуская (тарашкевіца)БългарскиभोजपुरीবাংলাBrezhonegBosanskiCatalàکوردیCorsuČeštinaKaszëbscziCymraegDanskDeutschZazaki

In [7]:
# Save the Polish and English segments to separate files
with open('hu_segments.txt', 'w', encoding='utf-8') as file:
    for segment in hu_segments:
        file.write(segment + '\n')

with open('en_segments.txt', 'w', encoding='utf-8') as file:
    for segment in en_segments:
        file.write(segment + '\n')

In [8]:
!hunalign/src/hunalign/hunalign hunalign/data/hu-en.stem.dic hu_segments.txt en_segments.txt -hand=hunalign/examples/demo.manual.ladder -text > align.txt

Reading dictionary...
59 source language sentences read.
379 target language sentences read.
Sizes differing too much. Ignoring files to avoid a rare loop bug.


### Ćwiczenie 4: Napisz konwerter formatu hunaligna na XLIFF.

In [9]:
import xml.etree.ElementTree as ET

def hunalign_to_xliff(hunalign_content, source_lang, target_lang, xliff_file):
    xliff = ET.Element('xliff', {
        'xmlns': 'urn:oasis:names:tc:xliff:document:1.2',
        'version': '1.2'
    })
    
    file_elem = ET.SubElement(xliff, 'file', {
        'datatype': 'plaintext',
        'original': 'self',
        'source-language': source_lang,
        'target-language': target_lang
    })
    
    header = ET.SubElement(file_elem, 'header')
    metadata = ET.SubElement(header, 'sxmd:metadata', {
        'xmlns:sxmd': 'urn:x-sap:mlt:xliff12:metadata:1.0',
        'xmlns': 'urn:x-sap:mlt:tsmetadata:1.0'
    })
    ET.SubElement(metadata, 'object-name').text = 'sample'
    ET.SubElement(metadata, 'collection').text = 'KWT'
    ET.SubElement(metadata, 'domain').text = 'KWT'
    ET.SubElement(metadata, 'developer').text = '123'
    ET.SubElement(metadata, 'description').text = 'sample XLIFF file'
    
    body = ET.SubElement(file_elem, 'body')
    
    for i, line in enumerate(hunalign_content.strip().split('\n')):
        src_tgt = line.strip().split(' ||| ')
        if len(src_tgt) == 2:
            trans_unit = ET.SubElement(body, 'trans-unit', {'id': str(i + 1)})
            ET.SubElement(trans_unit, 'source').text = src_tgt[0]
            ET.SubElement(trans_unit, 'target').text = src_tgt[1]
    
    tree = ET.ElementTree(xliff)
    ET.indent(tree, space="    ", level=0)  # Formatowanie z wcięciami
    tree.write(xliff_file, encoding='utf-8', xml_declaration=True)

In [10]:
hunalign_content = """
0-0 Hello world! ||| Witaj świecie!
1-1 This is a test. ||| To jest test.
2-2 How are you? ||| Jak się masz?
"""
hunalign_to_xliff(hunalign_content, 'en', 'pl', 'output.xliff')

In [11]:
with open("output.xliff", "r") as file:
    print(file.read())

<?xml version='1.0' encoding='utf-8'?>
<xliff xmlns="urn:oasis:names:tc:xliff:document:1.2" version="1.2">
    <file datatype="plaintext" original="self" source-language="en" target-language="pl">
        <header>
            <sxmd:metadata xmlns:sxmd="urn:x-sap:mlt:xliff12:metadata:1.0" xmlns="urn:x-sap:mlt:tsmetadata:1.0">
                <object-name>sample</object-name>
                <collection>KWT</collection>
                <domain>KWT</domain>
                <developer>123</developer>
                <description>sample XLIFF file</description>
            </sxmd:metadata>
        </header>
        <body>
            <trans-unit id="1">
                <source>0-0 Hello world!</source>
                <target>Witaj świecie!</target>
            </trans-unit>
            <trans-unit id="2">
                <source>1-1 This is a test.</source>
                <target>To jest test.</target>
            </trans-unit>
            <trans-unit id="3">
                <source>2-2 H